### Reingest missing sync sessions

In [11]:
from scripts.conf_file_finding import try_find_conf_file
try_find_conf_file()

Local configuration file found !!, no need to run the configuration (unless configuration has changed)


In [12]:
import numpy as np
import u19_pipeline.ephys_pipeline as ep
import u19_pipeline.recording as recording
import datajoint as dj
import pandas as pd
import datetime


In [13]:
#(ep.BehaviorSync & "recording_id=502").delete()

### Fetch all missing sync sessions

In [20]:
past_date = datetime.date.today() - datetime.timedelta(days=900)
query_session_date =  'session_date >="' + past_date.strftime('%Y-%m-%d') +'"'

all_recs = ((recording.Recording & "recording_modality='electrophysiology'") * (recording.Recording.BehaviorSession & query_session_date)).join(ep.BehaviorSync, left=True)
all_recs = pd.DataFrame(all_recs.fetch('recording_id','subject_fullname','session_date','session_number', as_dict=True))

not_sync_recs = pd.DataFrame((recording.Recording * ep.BehaviorSync).fetch('KEY', as_dict=True))

In [21]:
def get_rec_key_dict(recording_id):

    return {'recording_id': recording_id}

In [22]:
not_sync_recs2 = pd.merge(all_recs,not_sync_recs, how='left', indicator=True)
not_sync_recs2 = not_sync_recs2.loc[not_sync_recs2['_merge']=='left_only',:]
not_sync_recs2 = not_sync_recs2.sort_values(by='session_date', ascending=False)
not_sync_recs2['rec_key'] = not_sync_recs2['recording_id'].apply(get_rec_key_dict)
not_sync_recs2 = not_sync_recs2.reset_index(drop=True)
not_sync_recs2

recording_id             subject_fullname session_date  session_number  \
0           565                  emdia_penny   2026-01-06               0   
1           530                jk8386_jknpx6   2025-12-04               0   
2           401                    ms81_M031   2024-11-07               0   
3           242  testuser_automationpipeline   2023-09-08               0   

      _merge                rec_key  
0  left_only  {'recording_id': 565}  
1  left_only  {'recording_id': 530}  
2  left_only  {'recording_id': 401}  
3  left_only  {'recording_id': 242}

### Execute sync code

In [10]:
#for i in range(2):
ep.BehaviorSync.populate(not_sync_recs2.loc[8,'rec_key'])

{'recording_id': 502}
/mnt/cup/braininit/Data/Raw/electrophysiology/jyanar/jyanar_ya054/20251010_g0/ya054_20251010_g0
{'subject_fullname': 'jyanar_ya054', 'session_date': datetime.date(2025, 10, 10), 'session_number': 0}
len iterstart 309
after reading behavior data
nChan: 4, nFileSamp: 118289333
after reading spikeglx data
len trial_start_idx (309,)
mode deduction:  pulse_signal
trial# 2 iterPulses: 526 IterBeh: 527 Difference ( 1 )
trial# 3 iterPulses: 460 IterBeh: 525 Difference ( 65 )
trial# 27 iterPulses: 962 IterBeh: 965 Difference ( 3 )
trial# 32 iterPulses: 934 IterBeh: 935 Difference ( 1 )
trial# 35 iterPulses: 560 IterBeh: 561 Difference ( 1 )
trial# 40 iterPulses: 473 IterBeh: 474 Difference ( 1 )
trial# 51 iterPulses: 511 IterBeh: 512 Difference ( 1 )
trial# 60 iterPulses: 550 IterBeh: 551 Difference ( 1 )
trial# 77 iterPulses: 455 IterBeh: 456 Difference ( 1 )
trial# 81 iterPulses: 520 IterBeh: 521 Difference ( 1 )
trial# 84 iterPulses: 470 IterBeh: 472 Difference ( 2 )
tr

{'success_count': 1, 'error_list': []}

In [13]:
lo = (ep.BehaviorSync & "recording_id=502").fetch(as_dict=True)
lo[0]['sync_data']

{'trial_idx_vector': array([   981120,   1568269,   1855065,   2188393,   2521519,   2821749,
          3155021,   3432726,   3984339,   4346331,   4693225,   5057497,
          5376345,   5945483,   6284096,   6630595,   6957103,   7278161,
          7638156,   7952699,   8297375,   8599147,   8916890,   9291945,
          9655788,   9972014,  10300762,  10619423,  11164885,  11778993,
         12138278,  12486689,  13034929,  13564912,  13869827,  14189260,
         14524054,  14845048,  15185626,  15493292,  15834415,  16140612,
         16719103,  17283967,  17858440,  18238015,  18555303,  19158987,
         19496794,  19829392,  20230377,  20514165,  20840998,  21170533,
         21731610,  22041122,  22375554,  22715504,  23023445,  23351284,
         23685837,  24034565,  24398335,  24724261,  25032346,  25353516,
         25683070,  25994673,  26577758,  26914745,  27208812,  27540464,
         27899972,  28244907,  28567664,  28972442,  29299135,  29647992,
         29918134,

In [14]:
lo[0]['sync_data'].keys()

dict_keys(['trial_idx_vector', 'iteration_idx_vector', 'trial_idx_vector_from_virmen', 'iteration_idx_vector_from_virmen'])